1 Introduction
---
Given a new face image of a person, the task of face recognition is to recognize the human identity based on a relatively large training dataset, assuming the there are other face images of that person in the training dataset.

In this homework, we will build a model which is capable of recognizing and classifying a new image into predefined classes (the identity of persons apperaed in the training set).

2 Data Preparation and Visualization
---
We will use a subset of CroppedYale face dataset as our testbed. This dataset contains several persons' images with different illumination conditions. All the images are captured in frontal views therefore your model does not need to deal with image deformations.

In the first section, we will demonstrate how to load data and visualize it.


In [ ]:
# Download the CroppedYale face dataset.
!pip install wget
import wget
wget.download("https://tinyurl.com/4dshshxm", './CroppedYale.zip')
!unzip -q CroppedYale.zip

In [2]:
import os
import cv2
import numpy as np
from glob import glob
from matplotlib import pyplot as plt

In [3]:
# use a predefinted subset as the training/validation split
# there is no specific reason, just to make it easy to compare your results with the solution
subset_train = ['A+000E+00', 'A-010E+00', 'A+010E+00', 'A-005E+10', 'A+005E+10', 'A-005E-10', 'A+005E-10',
                'A+000E-20', 'A-010E-20', 'A+020E-10', 'A-025E+00', 'A-015E+20', 'A-020E-10', 'A+000E+20',
                'A+010E-20', 'A+020E+10', 'A+025E+00', 'A+015E+20', 'A-020E+10']
subset_valid = ['A+000E-35', 'A-035E+15', 'A-035E-20', 'A-020E-40', 'A-035E+40', 'A-050E+00', 'A+000E+45',
                'A+035E+15', 'A+035E-20', 'A+020E-40', 'A+035E+40', 'A+050E+00']
image_height, image_width = 96, 84

In [6]:
def load_yaleb_data(data_root):
    # scan over all the folders
    subject_list = glob(os.path.join(data_root, '*/'))
    image_train = np.zeros((image_height * image_width, 0))
    image_test = np.zeros((image_height * image_width, 0))
    label_train, label_test = [], []
    
    for idx, subject_path in enumerate(subject_list):
        print(f'Processing subject {idx + 1} / {len(subject_list)}')
        image_list = glob(os.path.join(subject_path, '*.pgm'))
        for im_path in image_list:
            im = cv2.resize(cv2.imread(im_path, cv2.IMREAD_GRAYSCALE), dsize=(image_height, image_width))
            im = im.reshape(-1)[:, None] / 255
            subject_name = im_path.split('/')[-1].split('.')[0].split('_')[1][3:]
            if subject_name in subset_train:
                image_train = np.concatenate([image_train, im], axis=1)
                label_train.append(idx)
            if subject_name in subset_valid:
                image_test = np.concatenate([image_test, im], axis=1)
                label_test.append(idx)

    return image_train, image_test, label_train, label_test

In [ ]:
image_train, image_test, label_train, label_test = load_yaleb_data('./CroppedYale/')
print(image_train.shape, image_test.shape)

Now we have 247 training images and 156 test images, each image is of (96 * 84) dimension. The image can be easily visualized using the following code:

In [ ]:
print(image_train.shape)
plt.imshow(image_train[:, 0].reshape(image_width, image_height), cmap='gray')
plt.show()

2 Methods
---
The core idea of using sparse represnetation to deal with the face recognition problem is: we assume the test image ($\mathbf{y} \in \mathbb{R}^{m}$, here $m = 96 \times 84$) of $i$-th class is a linear combination of the training samples of the $i$-th class. Denoting the training set as $A_i = [\mathbf{v}_{i, 1}, \mathbf{v}_{i,2}, \dots, \mathbf{v}_{i, n_i}]$, then
$$\mathbf{y} = \alpha_{i, 1} \mathbf{v}_{i,1} + \cdots + \alpha_{i, n_i} \mathbf{v}_{i, n_i}$$
for some scalars $\alpha_{i,j}\in \mathbb{R}$.

Since the membership $i$ of the test sample is initially unknown, we define a new matrix $\mathbf{A}$ for the entire training set as the concatenation of the $n$ training samples of all $k$ object classes:
$$A = [A_1, A_2, \cdots, A_k] = [v_{1,1}, \cdots, v_{1, n_1}, \cdots, v_{k, n_k}]$$

That is to say, 
$$\mathbf{y} = A \mathbf{x}_0$$ 

where $\mathbf{x}_0 = [0, \cdots, 0, \alpha_{i,1}, \alpha_{i,2}, \cdots, \alpha_{i, n_i}, 0, \cdots, 0]^\intercal \in \mathbb{R}^n$.

---

Therefore, we need to solve the following $\ell_1$-minimization problem:

$$\mathbf{\hat{x}}_1 = \arg\min ||\mathbf{x}||_1 \text{ subject to } \mathbf{Ax} = \mathbf{y}$$

However, it is not always possible to express $\mathbf{x}$ as the exact linear combination of training samples since real world data are usually noisy. We can modify the formulation to explicitly model the noise by writing:

$$\mathbf{y} = A \mathbf{x}_0 + z$$ 

where $z \in \mathbb{R}^m$ is a noise term with bounded energy $||z||_2 < \epsilon$. In this case, the sparse solution $\mathbf{x}_0$ can still be approximately recovered by solving:

$$\mathbf{\hat{x}}_1 = \arg\min ||\mathbf{x}||_1 \text{ subject to } ||\mathbf{Ax} - \mathbf{y}||_2 \leq \epsilon$$

---


3 Task 1: Implement Primal Augmented Lagrangian Method
---
Your task is to implement an optimization algorithm to deal with the above problem. There are varies way to tackle that such as ISTA algorithm. However, one more general choice would be the Algorithm 1 in https://arxiv.org/pdf/1007.3753.pdf, which is the primal augmented lagrangian method, which is used to solve

$$\min ||\mathbf{x}||_1 + ||\mathbf{e}||_1 \text{ subject to } Ax + e = y$$

Here we give an interface of this algorithm if you want to choose it. Note that it is not required to implement this algorithm, you can implement anyone you like as long as it can be used to solve the remaining tasks.

In [0]:
# you can modify the interface any way you like
# accelerated proximal gradient descent
def apg():
    return x

# primal augmented lagrangian method
def palm(y, A):
    # your code here
    alm_converge = False
    while not alm_converge:
        # your code here
        x = apg()
    return x, e

Task 1: Face Recognition without Corruption
---
In this section, we will do face recognition assuming there is no corruption of the image using your algorithm in section 2 and evaluate the accuracies of your model.


In [0]:
correct = 0
wrong = 0
for i in range(image_test.shape[1])
    y = image_test[:, i]
    x, e = palm(y, image_train)
    # your classification algorithm to check which class y belongs to
    # hint: compute the residual error for each each class
    c = your_cls_model(x, e)
    if c == label_test[i]:
        correct += 1
    else:
        wrong += 1

Task 2: Sparse Representation of Corrupted Image
---
In this section, we assume we already know the category of the test instance, but the image itself is corrupted. This is to say, you can put any image in part of the test image, and show the algorithm can still recover a sparse representation of the test image.

The portion of the occluded area is defined by the occl_size. You may put a 32 x 32 patch in the 96 x 84 face images, then in this case occl_size is 32.

You need to show what is the maximum occl_size your model can handle (essentially this means the classification result is still correct under occlusion)

In [0]:
def occlusion(y, occl_image, occl_size):
    return occlusion_y

In [0]:
j = 32
y = image_test[:, j]

# make the test image occluded by some random image
y = occlusion(y, occl_image, occl_size)

idx = np.where(np.array(label_train) == labeltest[test_image_index])
A_j = image_train[idx]
x, e = palm(y, A_j)

Varying the occlusion size, check in what range the algorithm will success / fail.

Task 3: Robust Face Recognition
---

Finally, you need to show the classification and recognition can be simultaneously solved by showing the classification accuracies on a corrupted test set.

In [0]:
y = occlusion(y, occu_image, occu_size)
x, e = palm(y, A)